# Welcome to a very busy Week 8 folder

## We have lots to do this week!

We'll move at a faster pace than usual, particularly as you're becoming proficient LLM engineers.


<table style="margin: 0; text-align: left;">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../important.jpg" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#900;">Especially important this week: pull the latest</h2>
            <span style="color:#900;">I'm continually improving these labs, adding more examples and exercises.
            At the start of each week, it's worth checking you have the latest code.<br/>
            First do a <a href="https://chatgpt.com/share/6734e705-3270-8012-a074-421661af6ba9">git pull and merge your changes as needed</a>. Any problems? Try asking ChatGPT to clarify how to merge - or contact me!<br/><br/>
            After you've pulled the code, from the llm_engineering directory, in an Anaconda prompt (PC) or Terminal (Mac), run:<br/>
            <code>conda env update --f environment.yml --prune</code><br/>
            Or if you used virtualenv rather than Anaconda, then run this from your activated environment in a Powershell (PC) or Terminal (Mac):<br/>
            <code>pip install -r requirements.txt</code>
            <br/>Then restart the kernel (Kernel menu >> Restart Kernel and Clear Outputs Of All Cells) to pick up the changes.
            </span>
        </td>
    </tr>
</table>

In [ ]:
# Just one import to start with!!

import modal

# Setting up the modal tokens

The first time you run this, please uncomment the next line and execute it.  
This is the same as running `modal setup` from the command line. It connects with Modal and installs your tokens.  

## Debugging some common problems on Windows

If this command fails in the next cell, or if any of the modal commands with the `!` fail, please try running them directly on the command line in an activated environment (without the `!`)

A student on Windows mentioned that on Windows, you might also need to run this command from a command prompt in an activated environment afterwards:  
`modal token new`  
(Thank you Ed B. for that!)

Another Windows student Minh N. mentioned you may need to use this approach, from an activated environment in the command line:  
`modal token set --token-id <your_token_id> --token-secret <your_token_secret>`

Also, a student David S. mentioned the following:  
> In case anyone else using Windows hits this problem: Along with having to run `modal token new` from a command prompt, you have to move the generated token file. It will deploy the token file (.modal.toml) to your Windows profile folder. The virtual environment couldn't see that location (strangely, it couldn't even after I set environment variables for it and rebooted). I moved that token file to the folder I'm operating out of for the lab and it stopped throwing auth errors.

And another Windows student (Robert M. - thank you!!) added another possible step:


> I could not get modal to see my tokens (resulting in an 'auth error'), even after copying the ".modal.toml" file to the "week8" folder and restarting JupyterLab. The fix was to manually set the environment variables (the standard way). This config method is explained by modal on their [web site](https://modal.com/docs/reference/modal.config)  
```
import os
os.environ["MODAL_TOKEN_ID"] = "xxx"
os.environ["MODAL_TOKEN_SECRET"] = "yyy" 
```

Finally: I've also heard that in some situations, you might need to restart the Kernel of this jupyter notebook after running this. (Kernel menu >> Restart Kernel and Clear Outputs of All Cells).

In [ ]:
# Remove the '# ' from the next line and run the cell, or run this command without the excalamation mark from an activated command prompt
# !modal setup

In [ ]:
from hello import app, hello, hello_europe

In [ ]:
with app.run():
    reply=hello.local()
reply

In [ ]:
with app.run():
    reply=hello.remote()
reply

## Added thanks to student Tue H.

If you look in hello.py, I've added a simple function hello_europe

That uses the decorator:  
`@app.function(image=image, region="eu")`

See the result below! More region specific settings are [here](https://modal.com/docs/guide/region-selection)

Note that it does consume marginally more credits to specify a region.

In [ ]:
with app.run():
    reply=hello_europe.remote()
reply

# Before we move on -

## We need to set your HuggingFace Token as a secret in Modal

1. Go to modal.com, sign in and go to your dashboard
2. Click on Secrets in the nav bar
3. Create new secret, click on Hugging Face, this new secret needs to be called **hf-secret** because that's how we refer to it in the code
4. Fill in your HF_TOKEN where it prompts you

### And now back to business: time to work with Llama

In [ ]:
from llama import app, generate

In [ ]:
with modal.enable_output():
    with app.run():
        result=generate.remote("Life is a mystery, everyone must stand alone, I hear")
result

In [ ]:
import modal
from pricer_ephemeral import app, price

In [ ]:
with modal.enable_output():
    with app.run():
        result=price.remote("Quadcast HyperX condenser mic, connects via usb-c to your computer for crystal clear audio")
result

## Transitioning From Ephemeral Apps to Deployed Apps

From a command line, `modal deploy xxx` will deploy your code as a Deployed App

This is how you could package your AI service behind an API to be used in a Production System.

You can also build REST endpoints easily, although we won't cover that as we'll be calling direct from Python.

## Important note for Windows people:

On the next line, I call `modal deploy` from within Jupyter lab; I've heard that on some versions of Windows this gives a strange unicode error because modal prints emojis to the output which can't be displayed. If that happens to you, simply use an Anaconda Prompt window or a Powershell instead, with your environment activated, and type `modal deploy pricer_service` there. Follow the same approach the next time we do `!modal deploy` too.

As an alternative, a few students have mentioned you can run this code within Jupyter Lab if you want to run it from here:
```
# Check the default encoding
print(locale.getpreferredencoding())  # Should print 'UTF-8'

# Ensure UTF-8 encoding
os.environ['PYTHONIOENCODING'] = 'utf-8'
```

In [ ]:
!modal deploy pricer_service

In [ ]:
pricer = modal.Function.lookup("pricer-service", "price")

In [ ]:
pricer.remote("Quadcast HyperX condenser mic, connects via usb-c to your computer for crystal clear audio")

In [ ]:
# You can also run "modal deploy -m pricer_service2" at the command line in an activated environment
!modal deploy -m pricer_service2

In [ ]:
Pricer = modal.Cls.lookup("pricer-service", "Pricer")
pricer = Pricer()
reply = pricer.price.remote("Quadcast HyperX condenser mic, connects via usb-c to your computer for crystal clear audio")
print(reply)

In [ ]:
!pip install --upgrade modal

# Optional: Keeping Modal warm

## A way to improve the speed of the Modal pricer service

A student mentioned to me that he was concerned by how slow Modal seems to be. The reason is that Modal puts our service to sleep if we don't use it, and then it takes 2.5 minutes to spin back up.

I've added a utility called `keep_warm.py` that will keep our Modal warm by pinging it every 30 seconds.

To use the utliity, bring up a new Terminal (Mac) or Anaconda prompt (Windows), ensure the environment is activated with `conda activate llms`

Then run: `python keep_warm.py` from within the week8 drectory.

Remember to press ctrl+C or exit the window when you no longer need Modal running.


## And now introducing our Agent class

In [ ]:
from agents.specialist_agent import SpecialistAgent

In [ ]:
agent = SpecialistAgent()
agent.price("iPad Pro 2nd generation")